from google.colab import drive

drive.mount('/content/drive')

!unzip /content/drive/MyDrive/data.zip

In [1]:
#train_raincityscapes_path = "/home/gregory/Documents/RainPerception/RainRemoval/Copied"

#test_raincityscapes_path = "/home/gregory/Documents/RainPerception/RainRemoval/Copied"

In [2]:
train_raincityscapes_path = "/home/gregory/Documents/RainPerception/RainRemoval/Copied"

test_raincityscapes_path = "/home/gregory/Documents/RainPerception/RainRemoval/Copied"

In [3]:
import datetime
import os
import torch
import os.path
from torch import nn
from torch import optim
from torch.autograd import Variable
from torch.backends import cudnn
from torch.utils.data import DataLoader
from torchvision import transforms
import random
from PIL import Image
import torch.nn.functional as F
import torch.utils.data as data
import numpy as np

In [4]:
class Compose(object):
    def __init__(self, transforms):
        self.transforms = transforms

    def __call__(self, img, mask, depth):
        assert img.size == mask.size
        assert img.size == depth.size
        for t in self.transforms:
            img, mask, depth = t(img, mask, depth)
        return img, mask, depth

class Resize(object):
    def __init__(self, size):
        self.size = tuple(reversed(size))  # size: (h, w)

    def __call__(self, img, mask, depth):
        assert img.size == mask.size
        assert img.size == depth.size
        return img.resize(self.size, Image.BILINEAR), mask.resize(self.size, Image.BILINEAR), depth.resize(self.size, Image.BILINEAR)


class RandomCrop(object):
    def __init__(self, size):
        self.size = size

    def __call__(self, img, mask, depth):
        assert img.size == mask.size
        assert img.size == depth.size
        w, h = img.size

        x1 = random.randint(0, w - self.size)
        y1 = random.randint(0, h - self.size)
        return img.crop((x1, y1, x1 + self.size, y1 + self.size)), mask.crop((x1, y1, x1 + self.size, y1 + self.size)), depth.crop((x1, y1, x1 + self.size, y1 + self.size))


class RandomHorizontallyFlip(object):
    def __call__(self, img, mask, depth):
        if random.random() < 0.5:
            return img.transpose(Image.FLIP_LEFT_RIGHT), mask.transpose(Image.FLIP_LEFT_RIGHT), depth.transpose(Image.FLIP_LEFT_RIGHT)
        return img, mask, depth

In [5]:
class AvgMeter(object):
    def __init__(self):
        self.reset()

    def reset(self):
        self.val = 0
        self.avg = 0
        self.sum = 0
        self.count = 0

    def update(self, val, n=1):
        self.val = val
        self.sum += val * n
        self.count += n
        self.avg = self.sum / self.count


def check_mkdir(dir_name):
    if not os.path.exists(dir_name):
        os.mkdir(dir_name)


class ReplayBuffer():
    def __init__(self, max_size=50):
        assert (max_size > 0), 'Empty buffer or trying to create a black hole. Be careful.'
        self.max_size = max_size
        self.data = []

    def push_and_pop(self, data):
        to_return = []
        for element in data.data:
            element = torch.unsqueeze(element, 0)
            if len(self.data) < self.max_size:
                self.data.append(element)
                to_return.append(element)
            else:
                if random.uniform(0,1) > 0.5:
                    i = random.randint(0, self.max_size-1)
                    to_return.append(self.data[i].clone())
                    self.data[i] = element
                else:
                    to_return.append(element)
        return Variable(torch.cat(to_return))


def mse_loss(input, target):
    return torch.sum((input - target)**2) / input.data.nelement()


def weights_init_normal(m):
    classname = m.__class__.__name__
    if classname.find('Conv') != -1:
        torch.nn.init.normal_(m.weight.data, 0.0, 0.02)
    elif classname.find('BatchNorm2d') != -1:
        torch.nn.init.normal_(m.weight.data, 1.0, 0.02)
        torch.nn.init.constant_(m.bias.data, 0.0)

In [6]:
def make_dataset(root, is_train):
    if is_train:

        input = open(os.path.join(root, 'data/train_images_both.txt'))
        ground_t = open(os.path.join(root, 'data/train_gt_both.txt'))
        depth_t = open(os.path.join(root, 'data/train_depth_both.txt'))
        image = [(os.path.join(root, 'data/images', img_name.strip('\n'))) for img_name in
                 input]
        gt = [(os.path.join(root, 'data/gt', img_name.strip('\n'))) for img_name in
                 ground_t]
        depth = [(os.path.join(root, 'data/depth', img_name.strip('\n'))) for img_name in
              depth_t]

        input.close()
        ground_t.close()
        depth_t.close()

        return [[image[i], gt[i], depth[i]]for i in range(len(image))]

    else:

        input = open(os.path.join(root, 'data/test_images_both.txt'))
        ground_t = open(os.path.join(root, 'data/test_gt_both.txt'))
        depth_t = open(os.path.join(root, 'data/test_depth_both.txt'))

        image = [(os.path.join(root, 'data/images', img_name.strip('\n'))) for img_name in
                 input]
        gt = [(os.path.join(root, 'data/gt', img_name.strip('\n'))) for img_name in
              ground_t]
        depth = [(os.path.join(root, 'data/depth', img_name.strip('\n'))) for img_name in
                 depth_t]

        input.close()
        ground_t.close()
        depth_t.close()
        
  
        return [[image[i], gt[i], depth[i]]for i in range(len(image))]



class ImageFolder(data.Dataset):
    def __init__(self, root, triple_transform=None, transform=None, target_transform=None, is_train=True):
        self.root = root
        self.imgs = make_dataset(root, is_train)
        self.triple_transform = triple_transform
        self.transform = transform
        self.target_transform = target_transform

    def __getitem__(self, index):
        img_path, gt_path, depth_path = self.imgs[index]
        
        img = Image.open(img_path)
        target = Image.open(gt_path)
        depth = Image.open(depth_path)

        if len(img.getbands()) == 4:
          temp = np.asarray(img)
          temp = temp[:,:,:3]
          img = Image.fromarray(temp)
        if len(target.getbands()) == 4:
          temp = np.asarray(target)
          temp = temp[:,:,:3]
          target = Image.fromarray(temp)
          
        if self.triple_transform is not None:
            img, target, depth = self.triple_transform(img, target, depth)
        if self.transform is not None:
            img = self.transform(img)
        if self.target_transform is not None:
            target = self.target_transform(target)
            depth = self.target_transform(depth)
          
        return img, target, depth

    def __len__(self):
        return len(self.imgs)

In [7]:
cudnn.benchmark = True

ckpt_path = '/home/gregory/Documents/RainPerception/RainRemoval/Copied/ckpt'
exp_name = 'DGNLNet'

args = {
    'iter_num': 42000,
    'train_batch_size': 4,
    'last_iter': 0,
    'lr': 5e-4,
    'lr_decay': 0.9,
    'weight_decay': 0,
    'momentum': 0.9,
    'resume_snapshot': '',
    'val_freq': 3000,
    'img_size_h': 512,
	'img_size_w': 1024,
	'crop_size': 512,
    'snapshot_epochs': 3000
}

In [8]:
transform = transforms.Compose([
    transforms.ToTensor()
    #transforms.Normalize([0.485, 0.456, 0.406], [0.229, 0.224, 0.225])
])
to_pil = transforms.ToPILImage()
triple_transform = Compose([
    Resize((args['img_size_h'], args['img_size_w'])),
    #triple_transforms.RandomCrop(args['crop_size']),
    RandomHorizontallyFlip()
])

In [9]:
train_set = ImageFolder(train_raincityscapes_path, transform=transform, target_transform=transform, is_train = True,triple_transform=triple_transform)
train_loader = DataLoader(train_set, batch_size=args['train_batch_size'], num_workers=4, shuffle=True)
test1_set = ImageFolder(test_raincityscapes_path, transform=transform, target_transform=transform, is_train=False)
test1_loader = DataLoader(test1_set, batch_size=2)

In [10]:
len(train_set)

27069

In [11]:
criterion = nn.L1Loss()
criterion_depth = nn.L1Loss()
log_path = os.path.join(ckpt_path, exp_name, str(datetime.datetime.now()) + '.txt')

In [12]:
class DGNL(nn.Module):
    def __init__(self, in_channels):
        super(DGNL, self).__init__()

        self.eps = 1e-6
        self.sigma_pow2 = 100

        self.theta = nn.Conv2d(in_channels, int(in_channels / 2), kernel_size=1)
        self.phi = nn.Conv2d(in_channels, int(in_channels / 2), kernel_size=1)
        self.g = nn.Conv2d(in_channels, int(in_channels / 2), kernel_size=1)

        self.down = nn.Conv2d(in_channels, in_channels, kernel_size=4, stride=4, groups=in_channels, bias=False)
        self.down.weight.data.fill_(1. / 16)

        self.z = nn.Conv2d(int(in_channels / 2), in_channels, kernel_size=1)



    def forward(self, x, depth_map):
        n, c, h, w = x.size()
        x_down = self.down(x)

		# [n, (h / 8) * (w / 8), c / 2]
        g = F.max_pool2d(self.g(x_down), kernel_size=2, stride=2).view(n, int(c / 2), -1).transpose(1, 2)

        ### appearance relation map
        # [n, (h / 4) * (w / 4), c / 2]
        theta = self.theta(x_down).view(n, int(c / 2), -1).transpose(1, 2)
        # [n, c / 2, (h / 8) * (w / 8)]
        phi = F.max_pool2d(self.phi(x_down), kernel_size=2, stride=2).view(n, int(c / 2), -1)

		# [n, (h / 4) * (w / 4), (h / 8) * (w / 8)]
        Ra = F.softmax(torch.bmm(theta, phi), 2)


        ### depth relation map
        depth1 = F.interpolate(depth_map, size=[int(h / 4), int(w / 4)], mode='bilinear', align_corners = True).view(n, 1, int(h / 4)*int(w / 4)).transpose(1,2)
        depth2 = F.interpolate(depth_map, size=[int(h / 8), int(w / 8)], mode='bilinear', align_corners = True).view(n, 1, int(h / 8)*int(w / 8))

        # n, (h / 4) * (w / 4), (h / 8) * (w / 8)
        depth1_expand = depth1.expand(n, int(h / 4) * int(w / 4), int(h / 8) * int(w / 8))
        depth2_expand = depth2.expand(n, int(h / 4) * int(w / 4), int(h / 8) * int(w / 8))

        Rd = torch.min(depth1_expand / (depth2_expand + self.eps), depth2_expand / (depth1_expand + self.eps))

        Rd = F.softmax(Rd, 2)

        S = F.softmax(Ra * Rd, 2)


        # [n, c / 2, h / 4, w / 4]
        y = torch.bmm(S, g).transpose(1, 2).contiguous().view(n, int(c / 2), int(h / 4), int(w / 4))

        return x + F.upsample(self.z(y), size=x.size()[2:], mode='bilinear', align_corners = True)



class NLB(nn.Module):
    def __init__(self, in_channels):
        super(NLB, self).__init__()
        self.theta = nn.Conv2d(in_channels, int(in_channels / 2), kernel_size=1)
        self.phi = nn.Conv2d(in_channels, int(in_channels / 2), kernel_size=1)
        self.g = nn.Conv2d(in_channels, int(in_channels / 2), kernel_size=1)

        self.down = nn.Conv2d(in_channels, in_channels, kernel_size=4, stride=4, groups=in_channels, bias=False)
        self.down.weight.data.fill_(1. / 16)

        self.z = nn.Conv2d(int(in_channels / 2), in_channels, kernel_size=1)

    def forward(self, x):
        n, c, h, w = x.size()
        x_down = self.down(x)

        # [n, (h / 4) * (w / 4), c / 2]
        theta = self.theta(x_down).view(n, int(c / 2), -1).transpose(1, 2)
        # [n, c / 2, (h / 8) * (w / 8)]
        phi = F.max_pool2d(self.phi(x_down), kernel_size=2, stride=2).view(n, int(c / 2), -1)
        # [n, (h / 8) * (w / 8), c / 2]
        g = F.max_pool2d(self.g(x_down), kernel_size=2, stride=2).view(n, int(c / 2), -1).transpose(1, 2)
        # [n, (h / 4) * (w / 4), (h / 8) * (w / 8)]
        f = F.softmax(torch.bmm(theta, phi), 2)
        # [n, c / 2, h / 4, w / 4]
        y = torch.bmm(f, g).transpose(1, 2).contiguous().view(n, int(c / 2), int(h / 4), int(w / 4))

        return x + F.upsample(self.z(y), size=x.size()[2:], mode='bilinear', align_corners=True)


class DepthWiseDilatedResidualBlock(nn.Module):
    def __init__(self, reduced_channels, channels, dilation):
        super(DepthWiseDilatedResidualBlock, self).__init__()
        self.conv0 = nn.Sequential(

		    # pw
		    nn.Conv2d(channels, channels * 2, 1, 1, 0, 1, bias=False),
			nn.ReLU6(inplace=True),
		    # dw
		    nn.Conv2d(channels*2, channels*2, kernel_size=3, padding=dilation, dilation=dilation, groups=channels, bias=False),
		    nn.ReLU6(inplace=True),
		    # pw-linear
		    nn.Conv2d(channels*2, channels, 1, 1, 0, 1, 1, bias=False)
        )

        self.conv1 = nn.Sequential(
	
			nn.Conv2d(channels, channels, kernel_size=3, padding=dilation, dilation=dilation, groups=channels,
					  bias=False),
			nn.ReLU6(inplace=True),
			# pw-linear
			nn.Conv2d(channels, channels, 1, 1, 0, 1, 1, bias=False)
		)


    def forward(self, x):
        res = self.conv1(self.conv0(x))
        return res + x


class DilatedResidualBlock(nn.Module):
    def __init__(self, channels, dilation):
        super(DilatedResidualBlock, self).__init__()
        self.conv0 = nn.Sequential(
            nn.Conv2d(channels, channels, kernel_size=3, padding=dilation, dilation=dilation), nn.ReLU()
        )
        self.conv1 = nn.Conv2d(channels, channels, kernel_size=3, padding=dilation, dilation=dilation)

    def forward(self, x):
        conv0 = self.conv0(x)
        conv1 = self.conv1(conv0)
        return x + conv1


class SpatialRNN(nn.Module):
	"""
	SpatialRNN model for one direction only
	"""
	def __init__(self, alpha = 1.0, channel_num = 1, direction = "right"):
		super(SpatialRNN, self).__init__()
		self.alpha = nn.Parameter(torch.Tensor([alpha] * channel_num))
		self.direction = direction

	def __getitem__(self, item):
		return self.alpha[item]

	def __len__(self):
		return len(self.alpha)


	def forward(self, x):
		"""
		:param x: (N,C,H,W)
		:return:
		"""
		height = x.size(2)
		weight = x.size(3)
		x_out = []

		# from left to right
		if self.direction == "right":
			x_out = [x[:, :, :, 0].clamp(min=0)]

			for i in range(1, weight):
				temp = (self.alpha.unsqueeze(1) * x_out[i - 1] + x[:, :, :, i]).clamp(min=0)
				x_out.append(temp)  # a list of tensor

			return torch.stack(x_out, 3)  # merge into one tensor

		# from right to left
		elif self.direction == "left":
			x_out = [x[:, :, :, -1].clamp(min=0)]

			for i in range(1, weight):
				temp = (self.alpha.unsqueeze(1) * x_out[i - 1] + x[:, :, :, -i - 1]).clamp(min=0)
				x_out.append(temp)

			x_out.reverse()
			return torch.stack(x_out, 3)

		# from up to down
		elif self.direction == "down":
			x_out = [x[:, :, 0, :].clamp(min=0)]

			for i in range(1, height):
				temp = (self.alpha.unsqueeze(1) * x_out[i - 1] + x[:, :, i, :]).clamp(min=0)
				x_out.append(temp)

			return torch.stack(x_out, 2)

		# from down to up
		elif self.direction == "up":
			x_out = [x[:, :, -1, :].clamp(min=0)]

			for i in range(1, height):
				temp = (self.alpha.unsqueeze(1) * x_out[i - 1] + x[:, :, -i - 1, :]).clamp(min=0)
				x_out.append(temp)

			x_out.reverse()
			return torch.stack(x_out, 2)

		else:
			print("Invalid direction in SpatialRNN!")
			return KeyError



class TVLoss(nn.Module):
    def __init__(self, tv_loss_weight=1):
        super(TVLoss, self).__init__()
        self.tv_loss_weight = tv_loss_weight

    def forward(self, x):
        batch_size = x.size()[0]
        h_x = x.size()[2]
        w_x = x.size()[3]
        count_h = self.tensor_size(x[:, :, 1:, :])
        count_w = self.tensor_size(x[:, :, :, 1:])
        h_tv = torch.pow((x[:, :, 1:, :] - x[:, :, :h_x - 1, :]), 2).sum()
        w_tv = torch.pow((x[:, :, :, 1:] - x[:, :, :, :w_x - 1]), 2).sum()
        return self.tv_loss_weight * 2 * (h_tv / count_h + w_tv / count_w) / batch_size

    @staticmethod
    def tensor_size(t):
        return t.size()[1] * t.size()[2] * t.size()[3]


class NLB(nn.Module):
    def __init__(self, in_channels):
        super(NLB, self).__init__()
        self.theta = nn.Conv2d(in_channels, int(in_channels / 2), kernel_size=1)
        self.phi = nn.Conv2d(in_channels, int(in_channels / 2), kernel_size=1)
        self.g = nn.Conv2d(in_channels, int(in_channels / 2), kernel_size=1)

        self.down = nn.Conv2d(in_channels, in_channels, kernel_size=4, stride=4, groups=in_channels, bias=False)
        self.down.weight.data.fill_(1. / 16)

        self.z = nn.Conv2d(int(in_channels / 2), in_channels, kernel_size=1)

    def forward(self, x):
        n, c, h, w = x.size()
        x_down = self.down(x)

        # [n, (h / 4) * (w / 4), c / 2]
        theta = self.theta(x_down).view(n, int(c / 2), -1).transpose(1, 2)
        # [n, c / 2, (h / 8) * (w / 8)]
        phi = F.max_pool2d(self.phi(x_down), kernel_size=2, stride=2).view(n, int(c / 2), -1)
        # [n, (h / 8) * (w / 8), c / 2]
        g = F.max_pool2d(self.g(x_down), kernel_size=2, stride=2).view(n, int(c / 2), -1).transpose(1, 2)
        # [n, (h / 4) * (w / 4), (h / 8) * (w / 8)]
        f = F.softmax(torch.bmm(theta, phi), 2)
        # [n, c / 2, h / 4, w / 4]
        y = torch.bmm(f, g).transpose(1, 2).contiguous().view(n, int(c / 2), int(h / 4), int(w / 4))

        return x + F.upsample(self.z(y), size=x.size()[2:], mode='bilinear', align_corners=True)

In [13]:
class DGNLNet_fast(nn.Module):
    def __init__(self, num_features=64):
        super(DGNLNet_fast, self).__init__()
        self.mean = torch.zeros(1, 3, 1, 1)
        self.std = torch.zeros(1, 3, 1, 1)
        self.mean[0, 0, 0, 0] = 0.485
        self.mean[0, 1, 0, 0] = 0.456
        self.mean[0, 2, 0, 0] = 0.406
        self.std[0, 0, 0, 0] = 0.229
        self.std[0, 1, 0, 0] = 0.224
        self.std[0, 2, 0, 0] = 0.225

        self.mean = nn.Parameter(self.mean)
        self.std = nn.Parameter(self.std)
        self.mean.requires_grad = False
        self.std.requires_grad = False

        ############################################ Depth prediction network
        self.conv1 = nn.Sequential(
			nn.Conv2d(3, 32, 8, stride=4, padding=2),
			nn.GroupNorm(num_groups=32, num_channels=32),
			nn.SELU(inplace=True)
		)

        self.conv2 = nn.Sequential(
			nn.Conv2d(32, 64, 4, stride=2, padding=1),
			nn.GroupNorm(num_groups=32, num_channels=64),
			nn.SELU(inplace=True)
		)

        self.conv3 = nn.Sequential(
			nn.Conv2d(64, 128, 4, stride=2, padding=1),
			nn.GroupNorm(num_groups=32, num_channels=128),
			nn.SELU(inplace=True)
		)

        self.conv5 = nn.Sequential(
			nn.Conv2d(128, 128, 3, padding=2, dilation=2),
			nn.GroupNorm(num_groups=32, num_channels=128),
			nn.SELU(inplace=True)
		)

        self.conv8 = nn.Sequential(
			nn.ConvTranspose2d(128, 64, kernel_size=4, stride=2, padding=1),
			nn.GroupNorm(num_groups=32, num_channels=64),
			nn.SELU(inplace=True)
		)

        self.conv9 = nn.Sequential(
			nn.ConvTranspose2d(64, 32, kernel_size=4, stride=2, padding=1),
			nn.GroupNorm(num_groups=32, num_channels=32),
			nn.SELU(inplace=True)
		)


        self.depth_pred = nn.Sequential(
			nn.Conv2d(32, 32, kernel_size=3, padding=1),
			nn.GroupNorm(num_groups=32, num_channels=32),
			nn.SELU(inplace=True),
			nn.Conv2d(32, 1, kernel_size=1, stride=1, padding=0),
			nn.Sigmoid()
		)

	############################################ Rain removal network


        self.head = nn.Sequential(
			# pw
			nn.Conv2d(3, 32, 1, 1, 0, 1, bias=False),
			nn.ReLU6(inplace=True),
			# dw
			nn.Conv2d(32, 32, kernel_size=8, stride=4, padding=2, groups=32, bias=False),
			nn.ReLU6(inplace=True),
			# pw-linear
			nn.Conv2d(32, num_features, 1, 1, 0, 1, 1, bias=False),
		)

        self.body = nn.Sequential(
			DepthWiseDilatedResidualBlock(num_features, num_features, 1),
			# DepthWiseDilatedResidualBlock(num_features, num_features, 1),
			DepthWiseDilatedResidualBlock(num_features, num_features, 2),
			DepthWiseDilatedResidualBlock(num_features, num_features, 2),
			DepthWiseDilatedResidualBlock(num_features, num_features, 4),
			DepthWiseDilatedResidualBlock(num_features, num_features, 8),
			DepthWiseDilatedResidualBlock(num_features, num_features, 4),
			DepthWiseDilatedResidualBlock(num_features, num_features, 2),
			DepthWiseDilatedResidualBlock(num_features, num_features, 2),
			# DepthWiseDilatedResidualBlock(num_features, num_features, 1),
			DepthWiseDilatedResidualBlock(num_features, num_features, 1)
		)


        self.dgnlb = DGNL(num_features)


        self.tail = nn.Sequential(
			# dw
			nn.ConvTranspose2d(num_features, 32, kernel_size=8, stride=4, padding=2, groups=32, bias=False),
			nn.ReLU6(inplace=True),
			# pw-linear
			nn.Conv2d(32, 3, 1, 1, 0, 1, bias=False),
		)

        for m in self.modules():
            if isinstance(m, nn.ReLU):
                m.inplace = True

    def forward(self, x):
        x = (x - self.mean) / self.std

        ################################## depth prediction
        d_f1 = self.conv1(x)
        d_f2 = self.conv2(d_f1)
        d_f3 = self.conv3(d_f2)
        d_f5 = self.conv5(d_f3)
        d_f8 = self.conv8(d_f5)
        d_f9 = self.conv9(d_f8 + d_f2)
        depth_pred = self.depth_pred(d_f9 + d_f1)

        ################################## rain removal

        f = self.head(x)
        f = self.body(f)
        f = self.dgnlb(f, depth_pred.detach())
        r = self.tail(f)
        x = x + r

        x = (x * self.std + self.mean).clamp(min=0, max=1)

        if self.training:
            return x, F.upsample(depth_pred, size=x.size()[2:], mode='bilinear', align_corners=True)

        return x



class DGNLNet(nn.Module):
    def __init__(self, num_features=64):
        super(DGNLNet, self).__init__()
        self.mean = torch.zeros(1, 3, 1, 1)
        self.std = torch.zeros(1, 3, 1, 1)
        self.mean[0, 0, 0, 0] = 0.485
        self.mean[0, 1, 0, 0] = 0.456
        self.mean[0, 2, 0, 0] = 0.406
        self.std[0, 0, 0, 0] = 0.229
        self.std[0, 1, 0, 0] = 0.224
        self.std[0, 2, 0, 0] = 0.225

        self.mean = nn.Parameter(self.mean)
        self.std = nn.Parameter(self.std)
        self.mean.requires_grad = False
        self.std.requires_grad = False

        ############################################ Depth prediction network
        self.conv1 = nn.Sequential(
			nn.Conv2d(3, 32, 4, stride=2, padding=1),
			nn.GroupNorm(num_groups=32, num_channels=32),
			nn.SELU(inplace=True)
		)

        self.conv2 = nn.Sequential(
			nn.Conv2d(32, 64, 4, stride=2, padding=1),
			nn.GroupNorm(num_groups=32, num_channels=64),
			nn.SELU(inplace=True)
		)

        self.conv3 = nn.Sequential(
			nn.Conv2d(64, 128, 4, stride=2, padding=1),
			nn.GroupNorm(num_groups=32, num_channels=128),
			nn.SELU(inplace=True)
		)

        self.conv4 = nn.Sequential(
			nn.Conv2d(128, 256, 4, stride=2, padding=1),
			nn.GroupNorm(num_groups=32, num_channels=256),
			nn.SELU(inplace=True)
		)

        self.conv5 = nn.Sequential(
			nn.Conv2d(256, 256, 3, padding=2, dilation=2),
			nn.GroupNorm(num_groups=32, num_channels=256),
			nn.SELU(inplace=True)
		)

        self.conv6 = nn.Sequential(
			nn.Conv2d(256, 256, 3, padding=4, dilation=4),
			nn.GroupNorm(num_groups=32, num_channels=256),
			nn.SELU(inplace=True)
		)

        self.conv7 = nn.Sequential(
			nn.Conv2d(256, 256, 3, padding=2, dilation=2),
			nn.GroupNorm(num_groups=32, num_channels=256),
			nn.SELU(inplace=True)
		)

        self.conv8 = nn.Sequential(
			nn.ConvTranspose2d(256, 128, kernel_size=4, stride=2, padding=1),
			nn.GroupNorm(num_groups=32, num_channels=128),
			nn.SELU(inplace=True)
		)

        self.conv9 = nn.Sequential(
			nn.ConvTranspose2d(128, 64, kernel_size=4, stride=2, padding=1),
			nn.GroupNorm(num_groups=32, num_channels=64),
			nn.SELU(inplace=True)
		)

        self.conv10 = nn.Sequential(
			nn.ConvTranspose2d(64, 32, kernel_size=4, stride=2, padding=1),
			nn.GroupNorm(num_groups=32, num_channels=32),
			nn.SELU(inplace=True)
		)

        self.depth_pred = nn.Sequential(
			nn.ConvTranspose2d(32, 32, kernel_size=4, stride=2, padding=1),
			nn.GroupNorm(num_groups=32, num_channels=32),
			nn.SELU(inplace=True),
			nn.Conv2d(32, 32, kernel_size=3, padding=1),
			nn.SELU(inplace=True),
			nn.Conv2d(32, 1, kernel_size=1, stride=1, padding=0),
			nn.Sigmoid()
		)

	############################################ Rain removal network

        self.head = nn.Sequential(
            nn.Conv2d(3, 32, kernel_size=4, stride=2, padding=1), nn.ReLU(),
            nn.Conv2d(32, num_features, kernel_size=1, stride=1, padding=0), nn.ReLU()
        )
        self.body = nn.Sequential(
            DilatedResidualBlock(num_features, 1),
            DilatedResidualBlock(num_features, 1),
            DilatedResidualBlock(num_features, 2),
            DilatedResidualBlock(num_features, 2),
            DilatedResidualBlock(num_features, 4),
            DilatedResidualBlock(num_features, 8),
            DilatedResidualBlock(num_features, 4),
            DilatedResidualBlock(num_features, 2),
            DilatedResidualBlock(num_features, 2),
            DilatedResidualBlock(num_features, 1),
            DilatedResidualBlock(num_features, 1)
        )

        self.dgnlb = DGNL(num_features)

        self.tail = nn.Sequential(
            # nn.Conv2d(num_features, num_features, kernel_size=3, padding=1), nn.ReLU(),
            nn.ConvTranspose2d(num_features, 32, kernel_size=4, stride=2, padding=1), nn.ReLU(),
            nn.Conv2d(32, 3, kernel_size=3, padding=1)
        )

        for m in self.modules():
            if isinstance(m, nn.ReLU):
                m.inplace = True

    def forward(self, x):
        x = (x - self.mean) / self.std

        ################################## depth prediction
        d_f1 = self.conv1(x)
        d_f2 = self.conv2(d_f1)
        d_f3 = self.conv3(d_f2)
        d_f4 = self.conv4(d_f3)
        d_f5 = self.conv5(d_f4)
        d_f6 = self.conv6(d_f5)
        d_f7 = self.conv7(d_f6)
        d_f8 = self.conv8(d_f7)
        d_f9 = self.conv9(d_f8 + d_f3)
        d_f10 = self.conv10(d_f9 + d_f2)
        depth_pred = self.depth_pred(d_f10 + d_f1)

        ################################## rain removal

        f = self.head(x)
        f = self.body(f)
        f = self.dgnlb(f, depth_pred.detach())
        r = self.tail(f)
        x = x + r

        x = (x * self.std + self.mean).clamp(min=0, max=1)

        if self.training:
            return x, depth_pred

        return x


class basic_NL(nn.Module):
    def __init__(self, num_features=64):
        super(basic_NL, self).__init__()
        self.mean = torch.zeros(1, 3, 1, 1)
        self.std = torch.zeros(1, 3, 1, 1)
        self.mean[0, 0, 0, 0] = 0.485
        self.mean[0, 1, 0, 0] = 0.456
        self.mean[0, 2, 0, 0] = 0.406
        self.std[0, 0, 0, 0] = 0.229
        self.std[0, 1, 0, 0] = 0.224
        self.std[0, 2, 0, 0] = 0.225

        self.mean = nn.Parameter(self.mean)
        self.std = nn.Parameter(self.std)
        self.mean.requires_grad = False
        self.std.requires_grad = False

        self.head = nn.Sequential(
            nn.Conv2d(3, 32, kernel_size=4, stride=2, padding=1), nn.ReLU(),
            nn.Conv2d(32, num_features, kernel_size=1, stride=1, padding=0), nn.ReLU()
        )
        self.body = nn.Sequential(
            DilatedResidualBlock(num_features, 1),
            DilatedResidualBlock(num_features, 1),
            DilatedResidualBlock(num_features, 2),
            DilatedResidualBlock(num_features, 2),
            DilatedResidualBlock(num_features, 4),
            DilatedResidualBlock(num_features, 8),
            DilatedResidualBlock(num_features, 4),
            DilatedResidualBlock(num_features, 2),
            DilatedResidualBlock(num_features, 2),
            DilatedResidualBlock(num_features, 1),
            DilatedResidualBlock(num_features, 1)
        )

        self.nlb = NLB(num_features)

        self.tail = nn.Sequential(
            # nn.Conv2d(num_features, num_features, kernel_size=3, padding=1), nn.ReLU(),
            nn.ConvTranspose2d(num_features, 32, kernel_size=4, stride=2, padding=1), nn.ReLU(),
            nn.Conv2d(32, 3, kernel_size=3, padding=1)
        )

        for m in self.modules():
            if isinstance(m, nn.ReLU):
                m.inplace = True

    def forward(self, x):
        x = (x - self.mean) / self.std

        f = self.head(x)
        f = self.body(f)
        f = self.nlb(f)
        r = self.tail(f)
        x = x + r

        x = (x * self.std + self.mean).clamp(min=0, max=1)
        return x



class basic(nn.Module):
    def __init__(self, num_features=64):
        super(basic, self).__init__()
        self.mean = torch.zeros(1, 3, 1, 1)
        self.std = torch.zeros(1, 3, 1, 1)
        self.mean[0, 0, 0, 0] = 0.485
        self.mean[0, 1, 0, 0] = 0.456
        self.mean[0, 2, 0, 0] = 0.406
        self.std[0, 0, 0, 0] = 0.229
        self.std[0, 1, 0, 0] = 0.224
        self.std[0, 2, 0, 0] = 0.225

        self.mean = nn.Parameter(self.mean)
        self.std = nn.Parameter(self.std)
        self.mean.requires_grad = False
        self.std.requires_grad = False

        self.head = nn.Sequential(
            nn.Conv2d(3, 32, kernel_size=4, stride = 2 ,padding=1), nn.ReLU(),
			nn.Conv2d(32, num_features, kernel_size=1, stride=1, padding=0), nn.ReLU()
        )
        self.body = nn.Sequential(
            DilatedResidualBlock(num_features, 1),
            DilatedResidualBlock(num_features, 1),
            DilatedResidualBlock(num_features, 2),
            DilatedResidualBlock(num_features, 2),
            DilatedResidualBlock(num_features, 4),
            DilatedResidualBlock(num_features, 8),
            DilatedResidualBlock(num_features, 4),
            DilatedResidualBlock(num_features, 2),
            DilatedResidualBlock(num_features, 2),
            DilatedResidualBlock(num_features, 1),
            DilatedResidualBlock(num_features, 1)
        )

        self.tail = nn.Sequential(
            #nn.Conv2d(num_features, num_features, kernel_size=3, padding=1), nn.ReLU(),
            nn.ConvTranspose2d(num_features, 32, kernel_size=4, stride=2, padding=1), nn.ReLU(),
            nn.Conv2d(32, 3, kernel_size=3, padding=1)
        )

        for m in self.modules():
            if isinstance(m, nn.ReLU):
                m.inplace = True

    def forward(self, x):
        x = (x - self.mean) / self.std

        f = self.head(x)
        f = self.body(f)
        r = self.tail(f)
        x = x + r

        x = (x * self.std + self.mean).clamp(min=0, max=1)
        return x



class depth_predciton(nn.Module):
    def __init__(self):
        super(depth_predciton, self).__init__()
        self.mean = torch.zeros(1, 3, 1, 1)
        self.std = torch.zeros(1, 3, 1, 1)
        self.mean[0, 0, 0, 0] = 0.485
        self.mean[0, 1, 0, 0] = 0.456
        self.mean[0, 2, 0, 0] = 0.406
        self.std[0, 0, 0, 0] = 0.229
        self.std[0, 1, 0, 0] = 0.224
        self.std[0, 2, 0, 0] = 0.225

        self.mean = nn.Parameter(self.mean)
        self.std = nn.Parameter(self.std)
        self.mean.requires_grad = False
        self.std.requires_grad = False


        self.conv1 = nn.Sequential(
            nn.Conv2d(3, 32, 4, stride=2, padding=1),
            nn.GroupNorm(num_groups=32, num_channels=32),
            nn.SELU(inplace=True)
        )

        self.conv2 = nn.Sequential(
            nn.Conv2d(32, 64, 4, stride=2, padding=1),
            nn.GroupNorm(num_groups=32, num_channels=64),
            nn.SELU(inplace=True)
        )

        self.conv3 = nn.Sequential(
            nn.Conv2d(64, 128, 4, stride=2, padding=1),
            nn.GroupNorm(num_groups=32, num_channels=128),
            nn.SELU(inplace=True)
        )

        self.conv4 = nn.Sequential(
            nn.Conv2d(128, 256, 4, stride=2, padding=1),
            nn.GroupNorm(num_groups=32, num_channels=256),
            nn.SELU(inplace=True)
        )

        self.conv5 = nn.Sequential(
            nn.Conv2d(256, 256, 3, padding=2, dilation=2),
            nn.GroupNorm(num_groups=32, num_channels=256),
            nn.SELU(inplace=True)
        )

        self.conv6 = nn.Sequential(
            nn.Conv2d(256, 256, 3, padding=4, dilation=4),
            nn.GroupNorm(num_groups=32, num_channels=256),
            nn.SELU(inplace=True)
        )

        self.conv7 = nn.Sequential(
            nn.Conv2d(256, 256, 3, padding=2, dilation=2),
            nn.GroupNorm(num_groups=32, num_channels=256),
            nn.SELU(inplace=True)
        )

        self.conv8 = nn.Sequential(
            nn.ConvTranspose2d(256, 128, kernel_size=4, stride=2, padding=1),
            nn.GroupNorm(num_groups=32, num_channels=128),
            nn.SELU(inplace=True)
        )

        self.conv9 = nn.Sequential(
            nn.ConvTranspose2d(128, 64, kernel_size=4, stride=2, padding=1),
            nn.GroupNorm(num_groups=32, num_channels=64),
            nn.SELU(inplace=True)
        )

        self.conv10 = nn.Sequential(
            nn.ConvTranspose2d(64, 32, kernel_size=4, stride=2, padding=1),
            nn.GroupNorm(num_groups=32, num_channels=32),
            nn.SELU(inplace=True)
        )

        self.depth_pred = nn.Sequential(
            nn.ConvTranspose2d(32, 32, kernel_size=4, stride=2, padding=1),
            nn.GroupNorm(num_groups=32, num_channels=32),
            nn.SELU(inplace=True),
            nn.Conv2d(32, 32, kernel_size=3, padding=1), nn.SELU(inplace=True),
            nn.Conv2d(32, 1, kernel_size=1, stride=1, padding=0),
            nn.Sigmoid()
        )


    def forward(self, x):

        x = (x - self.mean) / self.std

        d_f1 = self.conv1(x)
        d_f2 = self.conv2(d_f1)
        d_f3 = self.conv3(d_f2)
        d_f4 = self.conv4(d_f3)
        d_f5 = self.conv5(d_f4)
        d_f6 = self.conv6(d_f5)
        d_f7 = self.conv7(d_f6)
        d_f8 = self.conv8(d_f7)
        d_f9 = self.conv9(d_f8+d_f3)
        d_f10 = self.conv10(d_f9+d_f2)
        depth_pred = self.depth_pred(d_f10+d_f1)


        return depth_pred

In [14]:
def main():
    net = DGNLNet().cuda().train()
    net = nn.DataParallel(net)
    net.to(torch.device("cuda"))
    torch.cuda.empty_cache()

    optimizer = optim.Adam([
        {'params': [param for name, param in net.named_parameters() if name[-4:] == 'bias' and param.requires_grad],
         'lr': 2 * args['lr']},
        {'params': [param for name, param in net.named_parameters() if name[-4:] != 'bias' and param.requires_grad],
         'lr': args['lr'], 'weight_decay': args['weight_decay']}
    ])

    if len(args['resume_snapshot']) > 0:
        print('training resumes from \'%s\'' % args['resume_snapshot'])
        net.load_state_dict(torch.load(os.path.join(ckpt_path, exp_name, args['resume_snapshot'] + '.pth')))
        optimizer.load_state_dict(torch.load(os.path.join(ckpt_path, exp_name, args['resume_snapshot'] + '_optim.pth')))
        optimizer.param_groups[0]['lr'] = 2 * args['lr']
        optimizer.param_groups[1]['lr'] = args['lr']

    check_mkdir(ckpt_path)
    check_mkdir(os.path.join(ckpt_path, exp_name))
    open(log_path, 'w').write(str(args) + '\n\n')
    train(net, optimizer)

In [15]:
def train(net, optimizer):
    curr_iter = args['last_iter']
    while True:
        train_loss_record = AvgMeter()
        train_net_loss_record = AvgMeter()
        train_depth_loss_record = AvgMeter()

        for i, data in enumerate(train_loader):
            optimizer.param_groups[0]['lr'] = 2 * args['lr'] * (1 - float(curr_iter) / args['iter_num']
                                                                ) ** args['lr_decay']
            optimizer.param_groups[1]['lr'] = args['lr'] * (1 - float(curr_iter) / args['iter_num']
                                                            ) ** args['lr_decay']

            inputs, gts, dps = data
            batch_size = inputs.size(0)
            inputs = Variable(inputs).cuda()
            gts = Variable(gts).cuda()
            dps = Variable(dps).cuda()

            optimizer.zero_grad()

            result, depth_pred = net(inputs)

            loss_net = criterion(result, gts)
            loss_depth = criterion_depth(depth_pred, dps)

            loss = loss_net + loss_depth

            loss.backward()

            optimizer.step()

            train_loss_record.update(loss.data, batch_size)
            train_net_loss_record.update(loss_net.data, batch_size)
            train_depth_loss_record.update(loss_depth.data, batch_size)

            curr_iter += 1

            log = '[iter %d], [train loss %.5f], [lr %.13f], [loss_net %.5f], [loss_depth %.5f]' % \
                  (curr_iter, train_loss_record.avg, optimizer.param_groups[1]['lr'],
                   train_net_loss_record.avg, train_depth_loss_record.avg)
            print(log)
            open(log_path, 'a').write(log + '\n')

            if (curr_iter + 1) % args['val_freq'] == 0:
                validate(net, curr_iter, optimizer)

            if (curr_iter + 1) % args['snapshot_epochs'] == 0:
                torch.save(net.state_dict(), os.path.join(ckpt_path, exp_name, ('%d_test.pth' % (curr_iter + 1) )))
                torch.save(optimizer.state_dict(), os.path.join(ckpt_path, exp_name, ('%d_optim_test.pth' % (curr_iter + 1) )))

            if curr_iter > args['iter_num']:
                return

In [16]:
def validate(net, curr_iter, optimizer):
    print('validating...')
    net.eval()

    loss_record1, loss_record2 = AvgMeter(), AvgMeter()
    iter_num1 = len(test1_loader)

    with torch.no_grad():
        for i, data in enumerate(test1_loader):
            inputs, gts, dps = data
            inputs = Variable(inputs).cuda()
            gts = Variable(gts).cuda()
            dps = Variable(dps).cuda()

            res = net(inputs)

            loss = criterion(res, gts)
            loss_record1.update(loss.data, inputs.size(0))

            print('processed test1 %d / %d' % (i + 1, iter_num1))


    snapshot_name = 'iter_%d_loss1_%.5f_loss2_%.5f_lr_%.6f' % (curr_iter + 1, loss_record1.avg, loss_record2.avg,
                                                               optimizer.param_groups[1]['lr'])
    print('[validate]: [iter %d], [loss1 %.5f], [loss2 %.5f]' % (curr_iter + 1, loss_record1.avg, loss_record2.avg))
    torch.save(net.state_dict(), os.path.join(ckpt_path, exp_name, snapshot_name + '.pth'))
    torch.save(optimizer.state_dict(), os.path.join(ckpt_path, exp_name, snapshot_name + '_optim.pth'))

    net.train()

In [17]:
#import os
#os.environ['CUDA_VISIBLE_DEVICES'] = '0, 1, 2, 3'
#print(os.environ['CUDA_VISIBLE_DEVICES'])
#print(torch.cuda.is_available())


In [18]:
main()

/home/gregory/.local/lib/python3.7/site-packages/ipykernel_launcher.py:19: DeprecationWarning: BILINEAR is deprecated and will be removed in Pillow 10 (2023-07-01). Use Resampling.BILINEAR instead.
/home/gregory/.local/lib/python3.7/site-packages/ipykernel_launcher.py:19: DeprecationWarning: BILINEAR is deprecated and will be removed in Pillow 10 (2023-07-01). Use Resampling.BILINEAR instead.
/home/gregory/.local/lib/python3.7/site-packages/ipykernel_launcher.py:19: DeprecationWarning: BILINEAR is deprecated and will be removed in Pillow 10 (2023-07-01). Use Resampling.BILINEAR instead.
/home/gregory/.local/lib/python3.7/site-packages/ipykernel_launcher.py:39: DeprecationWarning: FLIP_LEFT_RIGHT is deprecated and will be removed in Pillow 10 (2023-07-01). Use Transpose.FLIP_LEFT_RIGHT instead.
/home/gregory/.local/lib/python3.7/site-packages/ipykernel_launcher.py:19: DeprecationWarning: BILINEAR is deprecated and will be removed in Pillow 10 (2023-07-01). Use Resampling.BILINEAR instea

[iter 1], [train loss 0.40568], [lr 0.0005000000000], [loss_net 0.08547], [loss_depth 0.32021]
[iter 2], [train loss 0.34978], [lr 0.0004999892857], [loss_net 0.06977], [loss_depth 0.28001]
[iter 3], [train loss 0.38150], [lr 0.0004999785714], [loss_net 0.08590], [loss_depth 0.29560]
[iter 4], [train loss 0.37859], [lr 0.0004999678570], [loss_net 0.08647], [loss_depth 0.29211]
[iter 5], [train loss 0.39350], [lr 0.0004999571427], [loss_net 0.09536], [loss_depth 0.29815]
[iter 6], [train loss 0.39564], [lr 0.0004999464283], [loss_net 0.09400], [loss_depth 0.30164]
[iter 7], [train loss 0.38946], [lr 0.0004999357138], [loss_net 0.09713], [loss_depth 0.29233]
[iter 8], [train loss 0.37913], [lr 0.0004999249994], [loss_net 0.09123], [loss_depth 0.28791]
[iter 9], [train loss 0.38652], [lr 0.0004999142849], [loss_net 0.09467], [loss_depth 0.29185]
[iter 10], [train loss 0.40176], [lr 0.0004999035704], [loss_net 0.10569], [loss_depth 0.29606]
[iter 11], [train loss 0.40354], [lr 0.0004998928

[iter 87], [train loss 0.36807], [lr 0.0004990784770], [loss_net 0.08592], [loss_depth 0.28216]
[iter 88], [train loss 0.36762], [lr 0.0004990677605], [loss_net 0.08582], [loss_depth 0.28180]
[iter 89], [train loss 0.36693], [lr 0.0004990570440], [loss_net 0.08548], [loss_depth 0.28144]
[iter 90], [train loss 0.36642], [lr 0.0004990463275], [loss_net 0.08525], [loss_depth 0.28117]
[iter 91], [train loss 0.36563], [lr 0.0004990356109], [loss_net 0.08484], [loss_depth 0.28079]
[iter 92], [train loss 0.36588], [lr 0.0004990248943], [loss_net 0.08466], [loss_depth 0.28122]
[iter 93], [train loss 0.36570], [lr 0.0004990141777], [loss_net 0.08437], [loss_depth 0.28133]
[iter 94], [train loss 0.36508], [lr 0.0004990034610], [loss_net 0.08428], [loss_depth 0.28079]
[iter 95], [train loss 0.36462], [lr 0.0004989927443], [loss_net 0.08403], [loss_depth 0.28059]
[iter 96], [train loss 0.36408], [lr 0.0004989820276], [loss_net 0.08393], [loss_depth 0.28015]
[iter 97], [train loss 0.36347], [lr 0.0

[iter 172], [train loss 0.34682], [lr 0.0004981674836], [loss_net 0.08305], [loss_depth 0.26377]
[iter 173], [train loss 0.34639], [lr 0.0004981567649], [loss_net 0.08301], [loss_depth 0.26338]
[iter 174], [train loss 0.34583], [lr 0.0004981460462], [loss_net 0.08291], [loss_depth 0.26292]
[iter 175], [train loss 0.34508], [lr 0.0004981353275], [loss_net 0.08268], [loss_depth 0.26240]
[iter 176], [train loss 0.34486], [lr 0.0004981246088], [loss_net 0.08276], [loss_depth 0.26210]
[iter 177], [train loss 0.34442], [lr 0.0004981138900], [loss_net 0.08263], [loss_depth 0.26179]
[iter 178], [train loss 0.34442], [lr 0.0004981031712], [loss_net 0.08290], [loss_depth 0.26152]
[iter 179], [train loss 0.34388], [lr 0.0004980924524], [loss_net 0.08281], [loss_depth 0.26107]
[iter 180], [train loss 0.34356], [lr 0.0004980817335], [loss_net 0.08275], [loss_depth 0.26080]
[iter 181], [train loss 0.34362], [lr 0.0004980710147], [loss_net 0.08307], [loss_depth 0.26055]
[iter 182], [train loss 0.3431

[iter 257], [train loss 0.32750], [lr 0.0004972563051], [loss_net 0.08091], [loss_depth 0.24659]
[iter 258], [train loss 0.32746], [lr 0.0004972455842], [loss_net 0.08105], [loss_depth 0.24641]
[iter 259], [train loss 0.32709], [lr 0.0004972348633], [loss_net 0.08093], [loss_depth 0.24616]
[iter 260], [train loss 0.32699], [lr 0.0004972241424], [loss_net 0.08085], [loss_depth 0.24613]
[iter 261], [train loss 0.32662], [lr 0.0004972134215], [loss_net 0.08073], [loss_depth 0.24588]
[iter 262], [train loss 0.32642], [lr 0.0004972027006], [loss_net 0.08081], [loss_depth 0.24561]
[iter 263], [train loss 0.32616], [lr 0.0004971919796], [loss_net 0.08075], [loss_depth 0.24541]
[iter 264], [train loss 0.32584], [lr 0.0004971812586], [loss_net 0.08068], [loss_depth 0.24516]
[iter 265], [train loss 0.32538], [lr 0.0004971705375], [loss_net 0.08058], [loss_depth 0.24480]
[iter 266], [train loss 0.32524], [lr 0.0004971598165], [loss_net 0.08076], [loss_depth 0.24448]
[iter 267], [train loss 0.3248

...

processed test1 2457 / 3860
processed test1 2458 / 3860
processed test1 2459 / 3860
processed test1 2460 / 3860
processed test1 2461 / 3860
processed test1 2462 / 3860
processed test1 2463 / 3860
processed test1 2464 / 3860
processed test1 2465 / 3860
processed test1 2466 / 3860
processed test1 2467 / 3860
processed test1 2468 / 3860
processed test1 2469 / 3860
processed test1 2470 / 3860
processed test1 2471 / 3860
processed test1 2472 / 3860
processed test1 2473 / 3860
processed test1 2474 / 3860
processed test1 2475 / 3860
processed test1 2476 / 3860
processed test1 2477 / 3860
processed test1 2478 / 3860
processed test1 2479 / 3860
processed test1 2480 / 3860
processed test1 2481 / 3860
processed test1 2482 / 3860
processed test1 2483 / 3860
processed test1 2484 / 3860
processed test1 2485 / 3860
processed test1 2486 / 3860
processed test1 2487 / 3860
processed test1 2488 / 3860
processed test1 2489 / 3860
processed test1 2490 / 3860
processed test1 2491 / 3860
processed test1 2492

processed test1 2750 / 3860
processed test1 2751 / 3860
processed test1 2752 / 3860
processed test1 2753 / 3860
processed test1 2754 / 3860
processed test1 2755 / 3860
processed test1 2756 / 3860
processed test1 2757 / 3860
processed test1 2758 / 3860
processed test1 2759 / 3860
processed test1 2760 / 3860
processed test1 2761 / 3860
processed test1 2762 / 3860
processed test1 2763 / 3860
processed test1 2764 / 3860
processed test1 2765 / 3860
processed test1 2766 / 3860
processed test1 2767 / 3860
processed test1 2768 / 3860
processed test1 2769 / 3860
processed test1 2770 / 3860
processed test1 2771 / 3860
processed test1 2772 / 3860
processed test1 2773 / 3860
processed test1 2774 / 3860
processed test1 2775 / 3860
processed test1 2776 / 3860
processed test1 2777 / 3860
processed test1 2778 / 3860
processed test1 2779 / 3860
processed test1 2780 / 3860
processed test1 2781 / 3860
processed test1 2782 / 3860
processed test1 2783 / 3860
processed test1 2784 / 3860
processed test1 2785

processed test1 3043 / 3860
processed test1 3044 / 3860
processed test1 3045 / 3860
processed test1 3046 / 3860
processed test1 3047 / 3860
processed test1 3048 / 3860
processed test1 3049 / 3860
processed test1 3050 / 3860
processed test1 3051 / 3860
processed test1 3052 / 3860
processed test1 3053 / 3860
processed test1 3054 / 3860
processed test1 3055 / 3860
processed test1 3056 / 3860
processed test1 3057 / 3860
processed test1 3058 / 3860
processed test1 3059 / 3860
processed test1 3060 / 3860
processed test1 3061 / 3860
processed test1 3062 / 3860
processed test1 3063 / 3860
processed test1 3064 / 3860
processed test1 3065 / 3860
processed test1 3066 / 3860
processed test1 3067 / 3860
processed test1 3068 / 3860
processed test1 3069 / 3860
processed test1 3070 / 3860
processed test1 3071 / 3860
processed test1 3072 / 3860
processed test1 3073 / 3860
processed test1 3074 / 3860
processed test1 3075 / 3860
processed test1 3076 / 3860
processed test1 3077 / 3860
processed test1 3078

processed test1 3336 / 3860
processed test1 3337 / 3860
processed test1 3338 / 3860
processed test1 3339 / 3860
processed test1 3340 / 3860
processed test1 3341 / 3860
processed test1 3342 / 3860
processed test1 3343 / 3860
processed test1 3344 / 3860
processed test1 3345 / 3860
processed test1 3346 / 3860
processed test1 3347 / 3860
processed test1 3348 / 3860
processed test1 3349 / 3860
processed test1 3350 / 3860
processed test1 3351 / 3860
processed test1 3352 / 3860
processed test1 3353 / 3860
processed test1 3354 / 3860
processed test1 3355 / 3860
processed test1 3356 / 3860
processed test1 3357 / 3860
processed test1 3358 / 3860
processed test1 3359 / 3860
processed test1 3360 / 3860
processed test1 3361 / 3860
processed test1 3362 / 3860
processed test1 3363 / 3860
processed test1 3364 / 3860
processed test1 3365 / 3860
processed test1 3366 / 3860
processed test1 3367 / 3860
processed test1 3368 / 3860
processed test1 3369 / 3860
processed test1 3370 / 3860
processed test1 3371

processed test1 3629 / 3860
processed test1 3630 / 3860
processed test1 3631 / 3860
processed test1 3632 / 3860
processed test1 3633 / 3860
processed test1 3634 / 3860
processed test1 3635 / 3860
processed test1 3636 / 3860
processed test1 3637 / 3860
processed test1 3638 / 3860
processed test1 3639 / 3860
processed test1 3640 / 3860
processed test1 3641 / 3860
processed test1 3642 / 3860
processed test1 3643 / 3860
processed test1 3644 / 3860
processed test1 3645 / 3860
processed test1 3646 / 3860
processed test1 3647 / 3860
processed test1 3648 / 3860
processed test1 3649 / 3860
processed test1 3650 / 3860
processed test1 3651 / 3860
processed test1 3652 / 3860
processed test1 3653 / 3860
processed test1 3654 / 3860
processed test1 3655 / 3860
processed test1 3656 / 3860
processed test1 3657 / 3860
processed test1 3658 / 3860
processed test1 3659 / 3860
processed test1 3660 / 3860
processed test1 3661 / 3860
processed test1 3662 / 3860
processed test1 3663 / 3860
processed test1 3664

In [25]:
import os
import time
import sys
import torch
from PIL import Image
from torch.autograd import Variable
from torchvision import transforms
from pathlib import Path
# from nets import DGNLNet_fast
# from misc import check_mkdir
import matplotlib.pyplot as plt

ckpt = "/home/gregory/Documents/RainPerception/RainRemoval/Copied/ckpt_day/DGNLNet/42000_test.pth"
#ckpt = "/home/gregory/Documents/RainPerception/RainRemoval/Copied/ckpt_night/DGNLNet/42000_test.pth"
#ckpt = "/home/gregory/Documents/RainPerception/RainRemoval/Copied/ckpt_both/DGNLNet/42000_test.pth"

#os.environ['CUDA_VISIBLE_DEVICES'] = '0'

torch.manual_seed(2019)
torch.cuda.set_device(0)

transform = transforms.Compose([
    transforms.Resize([512,1024]),
    transforms.ToTensor() ])

to_pil = transforms.ToPILImage()



if __name__ == '__main__':
    root = "/home/gregory/Documents/RainPerception/RainRemoval/Copied"
    input = open(os.path.join(root, 'data_test/test_images_day.txt'))
    i = 0
    image = [(os.path.join(root, 'data_test/images', img_name.strip('\n'))) for img_name in
                 input]
    input.close()

    # image = image[1000:]

    for img in image:
    # img = "/content/drive/MyDrive/test images/test_carla_H.png"

      net = DGNLNet().cuda()
      net = nn.DataParallel(net)
      net.to(torch.device("cuda"))

      net.load_state_dict(torch.load(ckpt,map_location=lambda storage,loc: storage.cuda(0)))

      net.eval()
      
      name = img.split("/")[-1]
      img = Image.open(Path(img))
      if len(img.getbands()) == 4:
        temp = np.asarray(img)
        temp = temp[:,:,:3]
        img = Image.fromarray(temp)
      # if isinstance(img,Image.Image):
      #     img = img.convert("RGB")
      # else:
      #     img = Image.open(Path(img))
      #     img = img.convert("RGB")
      # # plt.figure(figsize=(12,6))
      # plt.axis("off")
      # plt.imshow(img)
      with torch.no_grad():

          w, h = img.size
          img_var = Variable(transform(img).unsqueeze(0)).cuda()
          
          res = net(img_var)

          torch.cuda.synchronize()

          result = transforms.Resize((h, w))(to_pil(res.data.squeeze(0).cpu()))
          # fig = plt.figure(figsize=(16, 8))
          # fig.add_subplot(2,1,1)
          # plt.figure(figsize=(12,6))
          # plt.axis("off")
          # plt.imshow(img)
          # # fig.add_subplot(2,1,2)
          # plt.figure(figsize=(12,6))
          # plt.axis("off")
          # plt.imshow(result)
          i += 1
          print(i)
          result.save("/home/gregory/Documents/RainPerception/RainRemoval/Copied/generated_test_day/"+ name) 

1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
277


1861
1862
1863
1864
1865
1866
1867
1868
1869
1870
1871
1872
1873
1874
1875
1876
1877
1878
1879
1880
1881
1882
1883
1884
1885
1886
1887
1888
1889
1890
1891
1892
1893
1894
1895
1896
1897
1898
1899
1900
1901
1902
1903
1904
1905
1906
1907
1908
1909
1910
1911
1912
1913
1914
1915
1916
1917
1918
1919
1920
1921
1922
1923
1924
1925
1926
1927
1928
1929
1930
1931
1932
1933
1934
1935
1936
1937
1938
1939
1940
1941
1942
1943
1944
1945
1946
1947
1948
1949
1950
1951
1952
1953
1954
1955
1956
1957
1958
1959
1960
1961
1962
1963
1964
1965
1966
1967
1968
1969
1970
1971
1972
1973
1974
1975
1976
1977
1978
1979
1980
1981
1982
1983
1984
1985
1986
1987
1988
1989
1990
1991
1992
1993
1994
1995
1996
1997
1998
1999
2000
2001
2002
2003
2004
2005
2006
2007
2008
2009
2010
2011
2012
2013
2014
2015
2016
2017
2018
2019
2020
2021
2022
2023
2024
2025
2026
2027
2028
2029
2030
2031
2032
2033
2034
2035
2036
2037
2038
2039
2040
2041
2042
2043
2044
2045
2046
2047
2048
2049
2050
2051
2052
2053
2054
2055
2056
2057
2058
2059
2060


3500
3501
3502
3503
3504
3505
3506
3507
3508
3509
3510
3511
3512
3513
3514
3515
3516
3517
3518
3519
3520
3521
3522
3523
3524
3525
3526
3527
3528
3529
3530
3531
3532
3533
3534
3535
3536
3537
3538
3539
3540
3541
3542
3543
3544
3545
3546
3547
3548
3549
3550
3551
3552
3553
3554
3555
3556
3557
3558
3559
3560
3561
3562
3563
3564
3565
3566
3567
3568
3569
3570
3571
3572
3573
3574
3575
3576
3577
3578
3579
3580
3581
3582
3583
3584
3585
3586
3587
3588
3589
3590
3591
3592
3593
3594
3595
3596
3597
3598
3599
3600
3601
3602
3603
3604
3605
3606
3607
3608
3609
3610
3611
3612
3613
3614
3615
3616
3617
3618
3619
3620
3621
3622
3623
3624
3625
3626
3627
3628
3629
3630
3631
3632
3633
3634
3635
3636
3637
3638
3639
3640
3641
3642
3643
3644
3645
3646
3647
3648
3649
3650
3651
3652
3653
3654
3655
3656
3657
3658
3659
3660
3661
3662
3663
3664
3665
3666
3667
3668
3669
3670
3671
3672
3673
3674
3675
3676
3677
3678
3679
3680
3681
3682
3683
3684
3685
3686
3687
3688
3689
3690
3691
3692
3693
3694
3695
3696
3697
3698
3699


In [25]:
import os
import time
import sys
import torch
from PIL import Image
from torch.autograd import Variable
from torchvision import transforms
from pathlib import Path
# from nets import DGNLNet_fast
# from misc import check_mkdir
import matplotlib.pyplot as plt

#ckpt = "/home/gregory/Documents/RainPerception/RainRemoval/Copied/ckpt_day/DGNLNet/42000_test.pth"
#ckpt = "/home/gregory/Documents/RainPerception/RainRemoval/Copied/ckpt_night/DGNLNet/42000_test.pth"
ckpt = "/home/gregory/Documents/RainPerception/RainRemoval/Copied/ckpt_both/DGNLNet/42000_test.pth"

#os.environ['CUDA_VISIBLE_DEVICES'] = '0'

torch.manual_seed(2019)
torch.cuda.set_device(0)

transform = transforms.Compose([
    transforms.Resize([512,1024]),
    transforms.ToTensor() ])

to_pil = transforms.ToPILImage()



if __name__ == '__main__':
    root = "/home/gregory/Documents/RainPerception/RainRemoval/Copied"
    input = open(os.path.join(root, 'data_test/test_images_day.txt'))
    i = 0
    image = [(os.path.join(root, 'data_test/images', img_name.strip('\n'))) for img_name in
                 input]
    input.close()

    # image = image[1000:]

    for img in image:
    # img = "/content/drive/MyDrive/test images/test_carla_H.png"

      net = DGNLNet().cuda()
      net = nn.DataParallel(net)
      net.to(torch.device("cuda"))

      net.load_state_dict(torch.load(ckpt,map_location=lambda storage,loc: storage.cuda(0)))

      net.eval()
      
      name = img.split("/")[-1]
      img = Image.open(Path(img))
      if len(img.getbands()) == 4:
        temp = np.asarray(img)
        temp = temp[:,:,:3]
        img = Image.fromarray(temp)
      # if isinstance(img,Image.Image):
      #     img = img.convert("RGB")
      # else:
      #     img = Image.open(Path(img))
      #     img = img.convert("RGB")
      # # plt.figure(figsize=(12,6))
      # plt.axis("off")
      # plt.imshow(img)
      with torch.no_grad():

          w, h = img.size
          img_var = Variable(transform(img).unsqueeze(0)).cuda()
          
          res = net(img_var)

          torch.cuda.synchronize()

          result = transforms.Resize((h, w))(to_pil(res.data.squeeze(0).cpu()))
          # fig = plt.figure(figsize=(16, 8))
          # fig.add_subplot(2,1,1)
          # plt.figure(figsize=(12,6))
          # plt.axis("off")
          # plt.imshow(img)
          # # fig.add_subplot(2,1,2)
          # plt.figure(figsize=(12,6))
          # plt.axis("off")
          # plt.imshow(result)
          i += 1
          print(i)
          result.save("/home/gregory/Documents/RainPerception/RainRemoval/Copied/generated_test/"+ name) 

1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
277


1861
1862
1863
1864
1865
1866
1867
1868
1869
1870
1871
1872
1873
1874
1875
1876
1877
1878
1879
1880
1881
1882
1883
1884
1885
1886
1887
1888
1889
1890
1891
1892
1893
1894
1895
1896
1897
1898
1899
1900
1901
1902
1903
1904
1905
1906
1907
1908
1909
1910
1911
1912
1913
1914
1915
1916
1917
1918
1919
1920
1921
1922
1923
1924
1925
1926
1927
1928
1929
1930
1931
1932
1933
1934
1935
1936
1937
1938
1939
1940
1941
1942
1943
1944
1945
1946
1947
1948
1949
1950
1951
1952
1953
1954
1955
1956
1957
1958
1959
1960
1961
1962
1963
1964
1965
1966
1967
1968
1969
1970
1971
1972
1973
1974
1975
1976
1977
1978
1979
1980
1981
1982
1983
1984
1985
1986
1987
1988
1989
1990
1991
1992
1993
1994
1995
1996
1997
1998
1999
2000
2001
2002
2003
2004
2005
2006
2007
2008
2009
2010
2011
2012
2013
2014
2015
2016
2017
2018
2019
2020
2021
2022
2023
2024
2025
2026
2027
2028
2029
2030
2031
2032
2033
2034
2035
2036
2037
2038
2039
2040
2041
2042
2043
2044
2045
2046
2047
2048
2049
2050
2051
2052
2053
2054
2055
2056
2057
2058
2059
2060


3500
3501
3502
3503
3504
3505
3506
3507
3508
3509
3510
3511
3512
3513
3514
3515
3516
3517
3518
3519
3520
3521
3522
3523
3524
3525
3526
3527
3528
3529
3530
3531
3532
3533
3534
3535
3536
3537
3538
3539
3540
3541
3542
3543
3544
3545
3546
3547
3548
3549
3550
3551
3552
3553
3554
3555
3556
3557
3558
3559
3560
3561
3562
3563
3564
3565
3566
3567
3568
3569
3570
3571
3572
3573
3574
3575
3576
3577
3578
3579
3580
3581
3582
3583
3584
3585
3586
3587
3588
3589
3590
3591
3592
3593
3594
3595
3596
3597
3598
3599
3600
3601
3602
3603
3604
3605
3606
3607
3608
3609
3610
3611
3612
3613
3614
3615
3616
3617
3618
3619
3620
3621
3622
3623
3624
3625
3626
3627
3628
3629
3630
3631
3632
3633
3634
3635
3636
3637
3638
3639
3640
3641
3642
3643
3644
3645
3646
3647
3648
3649
3650
3651
3652
3653
3654
3655
3656
3657
3658
3659
3660
3661
3662
3663
3664
3665
3666
3667
3668
3669
3670
3671
3672
3673
3674
3675
3676
3677
3678
3679
3680
3681
3682
3683
3684
3685
3686
3687
3688
3689
3690
3691
3692
3693
3694
3695
3696
3697
3698
3699


In [20]:
import os
import time
import sys
import torch
from PIL import Image
from torch.autograd import Variable
from torchvision import transforms
from pathlib import Path
# from nets import DGNLNet_fast
# from misc import check_mkdir
import matplotlib.pyplot as plt

ckpt = "/home/gregory/Documents/RainPerception/RainRemoval/Copied/ckpt/DGNLNet/22_test.pth"

#os.environ['CUDA_VISIBLE_DEVICES'] = '0'

#torch.manual_seed(2019)
#torch.cuda.set_device(0)

transform = transforms.Compose([
    transforms.Resize([512,1024]),
    transforms.ToTensor() ])

to_pil = transforms.ToPILImage()



if __name__ == '__main__':
    root = "/home/gregory/Documents/RainPerception/RainRemoval/Copied"
    
    
    img = "/home/gregory/Documents/RainPerception/RainRemoval/Copied/generated_test/1647760644.0353005_rain_M.png"

    # net = DGNLNet().cuda()

    # net.load_state_dict(torch.load(ckpt,map_location=lambda storage,loc: storage.cuda(0)))

    # net.eval()
    
    # name = img.split("/")[-1]
    img = Image.open(Path(img))
    if len(img.getbands()) == 4:
      temp = np.asarray(img)
      temp = temp[:,:,:3]
      img = Image.fromarray(temp)
    if isinstance(img,Image.Image):
        img = img.convert("RGB")
    else:
        img = Image.open(Path(img))
        img = img.convert("RGB")
    # # # plt.figure(figsize=(12,6))
    # # plt.axis("off")
    # # plt.imshow(img)
    # with torch.no_grad():

    #     w, h = img.size
    #     img_var = Variable(transform(img).unsqueeze(0)).cuda()
        
    #     res = net(img_var)

    #     torch.cuda.synchronize()

    #     result = transforms.Resize((h, w))(to_pil(res.data.squeeze(0).cpu()))
    #     fig = plt.figure(figsize=(16, 8))
    #     fig.add_subplot(2,1,1)
    #     plt.figure(figsize=(12,6))
    #     plt.axis("off")
    #     plt.imshow(img)
    #     # fig.add_subplot(2,1,2)
    #     plt.figure(figsize=(12,6))
    #     plt.axis("off")
    #     plt.imshow(result)

FileNotFoundError: [Errno 2] No such file or directory: '/home/gregory/Documents/RainPerception/RainRemoval/Copied/generated_test/1647760644.0353005_rain_M.png'

In [21]:
import cv2
import math
import numpy as np

def ssim(img1,img2):

    C1 = (0.01 * 255)**2
    C2 = (0.03 * 255)**2

    img1 = img1.astype(np.float64)
    img2 = img2.astype(np.float64)
    kernel = cv2.getGaussianKernel(11, 1.5)
    window = np.outer(kernel, kernel.transpose())

    mu1 = cv2.filter2D(img1, -1, window)[5:-5, 5:-5]  # valid
    mu2 = cv2.filter2D(img2, -1, window)[5:-5, 5:-5]
    mu1_sq = mu1**2
    mu2_sq = mu2**2
    mu1_mu2 = mu1 * mu2

    sigma1_sq = cv2.filter2D(img1**2, -1, window)[5:-5, 5:-5] - mu1_sq
    sigma2_sq = cv2.filter2D(img2**2, -1, window)[5:-5, 5:-5] - mu2_sq
    sigma12 = cv2.filter2D(img1 * img2, -1, window)[5:-5, 5:-5] - mu1_mu2

    ssim_map = ((2 * mu1_mu2 + C1) * (2 * sigma12 + C2)) / ((mu1_sq + mu2_sq + C1) *
                                                            (sigma1_sq + sigma2_sq + C2))
    return ssim_map.mean()

def psnr(img1,img2):

    img1 = img1.astype(np.float64)
    img2 = img2.astype(np.float64)
    mse = np.mean((img1 - img2)**2)
    if mse == 0:
        return float('inf')
    return 20 * math.log10(255.0 / math.sqrt(mse))

In [23]:
img1 = cv2.imread("/home/gregory/Documents/RainPerception/RainRemoval/Copied/data/images/val/carla/1647760470.3255076_rain_H.png")
img2 = cv2.imread("/home/gregory/Documents/RainPerception/RainRemoval/Copied/generated_test_both/1647760470.3255076_rain_H.png")

psnr(img1,img2),ssim(img1,img2)

AttributeError: 'NoneType' object has no attribute 'astype'

In [ ]:
import os
import time
import sys
import torch
from PIL import Image
from torch.autograd import Variable
from torchvision import transforms
from pathlib import Path
import matplotlib.pyplot as plt
import numpy as np
# from nets import DGNLNet

class RainRemoval:
    def __init__(self,model):
        self.model = model

    def infer(self,img,flag = True):

        os.environ['CUDA_VISIBLE_DEVICES'] = '0'

        torch.manual_seed(2019)
        torch.cuda.set_device(0)

        transform = transforms.Compose([
            transforms.Resize([512,1024]),
            transforms.ToTensor() ])

        to_pil = transforms.ToPILImage()    


        if type(img) == str:
          img = np.asarray(Image.open(img))
          
        net = DGNLNet().cuda()

        net.load_state_dict(torch.load(self.model,map_location=lambda storage,loc: storage.cuda(0)))

        net.eval()

        if img.shape[-1] == 4:
            img = img[:,:,:-1]

        self.img_infer = Image.fromarray(img)

        with torch.no_grad():

            w, h = self.img_infer.size
            img_var = Variable(transform(self.img_infer).unsqueeze(0)).cuda()
            
            res = net(img_var)

            torch.cuda.synchronize()

            self.result = transforms.Resize((h, w))(to_pil(res.data.squeeze(0).cpu()))

            self.result_np = np.array(self.result)
        
        if flag:
            return self.result_np
        else:
            return self.result
    
    def displayRes(self):

        fig = plt.figure(figsize=(14, 7))
        
        fig.add_subplot(1,2,1)
        plt.axis("off")
        plt.imshow(self.img_infer)
        
        fig.add_subplot(1,2,2)
        plt.axis("off")
        plt.imshow(self.result)